# gCube CMS

<strong>gCube CMS</strong> is a software application that allows users to collaborate in the creation, editing, and production of complex digital components called <strong> Projects</strong>.

The application is built on top of <strong>gCube Infrastructure</strong> features, for maximum integration with <strong>Virtual Research Environments (VREs)</strong> and supports : 
- <strong>Complex Data Management</strong> : Projects are made of core Metadata, custom Metadata, multiple linked FileSets
- <strong>Versioning, Workflows, Access Policies</strong> integrated with the Infrastructure User Role Management
- <strong>Materializations</strong> (e.g. SDI Layer, Image Thumbnail, DBMS)
- <strong>Indexing</strong> (e.g. GIS Catalogues, Centroids Layer, CKAN catalogue)
- <strong>Event Triggering</strong> (e.g. Notifications)

The application is comprised of various components, including : 
- <strong>GUIs</strong> to facilitate end users in managing and consuming Projects
- <strong>Service</strong> implemented the core business logic
- <strong>Plugins</strong> set of modular logic implementations (both general-purpose and custom-made) aimed at dealing with Projects Lifecycle Phases and Events

![Concept](https://gcube.wiki.gcube-system.org/images_gcube/a/a3/DataCube.png)

## Parameters Init

Customize this section for different notebook behaviour and initialization.

In [ ]:
import requests
import json

# These parameters should be discovered / initialized by common gcube libraries. 
gcube_token = "..."
service_base_endpoint ="https://geoportal.dev.int.d4science.net/geoportal-service/srv"

# Actual customizable parameters
ucid = "basic"


#NB The following should not be changed 
projects_endpoint = service_base_endpoint + "/projects/"+ucid
ucd_endpoint = service_base_endpoint + "/ucd/"
plugins_endpoint=service_base_endpoint + "/plugins/"


## Import Rich text support for pretty json 
!pip install rich[jupyter]
import rich
from rich import print_json

## Define utility function for HTTP requests logging
def send(dest,data=None,method="GET",params={}):
    print("GOING TO SEND "+method+" REQUEST TO "+dest)
    headers={
        'Content-type':'application/json', 
        'Accept':'*/*',
        'gcube-token':gcube_token
    }
    if data is not None : print("Data is "+str(data))
    if method == "GET" : response = requests.get(url=dest,params=params,headers=headers)
    if method == "PUT" : response = requests.put(url=dest,data=data,params=params,headers=headers)
    if method == "POST" : response = requests.post(url=dest,data=data,params=params,headers=headers)
    if method == "DELETE" : response = requests.delete(url=dest,data=data,params=params,headers=headers)
    print("RESPONSE STATUS "+str(response.status_code))    
    if response.status_code<200 or response.status_code>=300 : 
           print("CAUSE "+str(response.reason))
           print(response.text)
    return json.loads(response.text)

#print(send(method="GET",dest="http://geoportal.dev.int.d4science.net/geoportal-service/srv/mongo-concessioni/"))

# Projects

<strong>Projects</strong> are the main entities in gCube CMS. They represent a complex document comprising of its metadata, its datasets, and related information aimed at properly consume them.\ 
The present section guides through the management of CMS Projects, explaining it's model and all supported operations.

<strong>Projects </strong> enacapsulate user's JSON Document in a richer format comprising : 
- <strong>Core Metadata</strong> : Metadata information used by the service to manage the project lifecycle
- <strong>The Document</strong> : A JSON Object compliant to user's defined schema, reporting both 
 - The actual metadata regarding the managed documents
 - Attachments references to payloads and generated materializations

Projects are linked to <strong>Use Case Descriptors (UCD)</strong>, which define how its Document contents are gonna be treated in the system.

More detailed informations can be found at https://gcube.wiki.gcube-system.org/gcube/GeoPortal_Service

<strong>NB</strong>: In this notebook we are going to use the UCD "basicUCD". If you want to learn more about UCDs, please refer to wiki pages or related notebooks.

<strong>NB</strong>: User can experiment with different UCDs but they need to be published in the current infrastructure's Context.

## Create New
Start This tutorial by creating your new Project.

In this section we are going to <strong>create</strong> a new simple document and inspect the result. 
You will learn the basic sections of a Project Metadata and their meaning.

It is sufficient to perform a <strong>post</strong> operation with our document as the body.

The REST base endpoint for managing projects is <em>SERVICE_BASE_ENDPOINT</em>/<strong>projects</strong>/UCID where:\
- SERVICE_BASE_ENDPOINT should be discovered from the infrastructure's Information System
- UCID is the ID of the Use Case Descriptor to be used with this project

In [ ]:
# Edit this section to customize your document
doc={"myTitle":"Some Big Title"}

In [ ]:
project= send(method="POST",dest=projects_endpoint,data=json.dumps(doc))

print("Resulting project is ")
print_json(data=project)

## Core Metadata Section
Registered JSON Documents are wrapped in Projects, which Let's inspect the registered JSON object structure and the most useful information in it.

The field <strong>_theDocument</strong> represents our document of interest.

<strong>NB</strong> : Depending on the linked UCD, the returned document might be different from the output.\
This is due to the fact that the UCD is configured to automatically perform some operation at creation time (e.g. "set defaults values")

In [ ]:
print_json(data=project["_theDocument"])

### ID
The field <strong>_id</strong> is the unique identifier of the project.\
We are gonna use it for all REST operations that involves our project.

In [ ]:
print_json(data=project["_id"])

### Accounting Information

The field <strong>_info</strong> contains the following accounting information related to the project : 
- <strong>_creationInfo</strong> : user, context and instant of creation
- <strong>_lastEditInfo</strong> : user, context and instant of last edit operation
- <strong>_access</strong> : project access policy (can be OPEN, RESTRICTED or EMBARGOED), project license

In [ ]:
print_json(data=project["_info"])

### Lifecycle Information 
The field <strong>_lifecycleInformation</strong> contains the a structured report of the status of the project containing: 
- <strong>_phase</strong> : The workflow <strong>phase</strong> in which the document is at the moment
- <strong>_lastInvokedStep</strong> : Report on the last executed workflow <strong>STEP</strong>
- <strong>_triggeredEvents</strong> : Collections of reports regarding the triggered events
- <strong>_notes</strong> : User defined notes on the status of the project
- <strong>_errorMessages</strong> : Human readable error messages, if any
- <strong>_warningMessages</strong> : Human readable warning messages, if any

See Plugins section for more information.

In [ ]:
print_json(data=project["_lifecycleInformation"])

### Spatial Reference
The field <strong>_spatialReference</strong> contains a GEOJSON geometry identifying the Project.

E.g. like the following : 

```json
"_spatialReference":
  {
    "type": "Point",
    "bbox":
    [
      8.621178639172953,
      40.62975046683799,
      40.630257904721645,
      8.62091913167495
    ],
    "coordinates":
    [
      -32.00907926554869,
      -32.00883133516304
    ]
  }
```


### Temporal Reference 
TBD

## Editing a project
Edit the Document section of a Project. 

The Document section is the actual document that needs to be managed, and the most basic operation is updating it.\
To do this it's sufficient to perform a <strong>put</strong> operation with our document as the body, specifying our project's <strong>ID</strong>

The endpoint for this operation is going to be <em>SERVICE_BASE_ENDPOINT</em>/projects/UCID/<strong>ID</strong> where:
- SERVICE_BASE_ENDPOINT should be discovered from the infrastructure's Information System
- UCID is the ID of the Use Case Descriptor to be used with this project
- ID is our project Unique Identifier

In [ ]:
#We update our document nesting a sub section in it
doc={
    "myTitle":"My newer edited title",
    "section":{"sectionTitle":"My new SubSection"}
}

In [ ]:
# NB uncomment to actually perform edit
project = send(method="PUT",data=json.dumps(doc),dest=projects_endpoint+"/"+str(project["_id"]))
print_json(data=project["_theDocument"])

## Upload Attachments : FileSets
Projects' documents can contain multiple collections of files called FileSet.

We use the concept of <strong>FileSet</strong> to identify a collection of files that should be managed together (e.g. GIS shape file along with its SHX file).\
In this section we are going to <strong>register a FileSet</strong> in our project.\

The operations triggers :
- the upload and archive of passed data streams
- registration of the file in "_theDocument", precisely at the JSON path declared in the request

<strong>NB<strong> Please beware that FileSet JSON paths <strong>MUST</strong> be deined in our UCD schema section.

In order to perform this operation we are going to create a JSON object request with at least the following information : 
- <strong>fieldDefinitionPath</strong> : a JSON path pointing to the field definition in UCD schema [NB root is "schema"]
- <strong>parentPath</strong> : a JSON path pointing to the parent of our target element [NB root is "_theDocument"]
- <strong>fieldName</strong> : the target element name at which the FileSet is going to be registered
- <strong>streams</strong> : a collection of JSON objects, each containing
 - <strong>id</strong> : the infrastructure <strong>STORAGE volatile ID</strong> of our File
 - <strong>url</strong> : [Alternative to ID] the url at which our File can be downloaded.
 - <strong>filename</strong> : our File name

In [ ]:
registerFilesetRequest={
    "fieldDefinitionPath":"$.section._children[?(@.fileset)]",
    "parentPath":"$.section",
    "fieldName":"fileset",
    "streams":[{"url":"https://www.cnr.it/sites/all/themes/custom/cnr03_theme/img/cnrlogo.svg","filename":"myLogo.svg"}]
}

Once our request is ready we can send it to server with a <strong>POST</strong> request at <em>SERVICE_BASE_ENDPOINT</em>/projects/UCID/registerFiles/<strong>ID</strong> where:\
- SERVICE_BASE_ENDPOINT should be discovered from the infrastructure's Information System
- UCID is the ID of the Use Case Descriptor to be used with this project
- ID is our project Unique Identifier

In [ ]:
project = send(method="POST",dest=projects_endpoint+"/registerFiles/"+str(project["_id"]),data=json.dumps(registerFilesetRequest))

print("Our Registered FileSet")
print_json(data=project["_theDocument"]["section"]["fileset"])

## Workflow operation : Execute STEP
Execute operations on a Project in order to manage its lifecycle

Projects lifecycle may involve a lot of operations (usually perfomed by different users), that should be perfomed in a pre defined order eg : 
- registration
- approval
- rejection
- validation
- notifications
- processing : 
 - materialization of Fileset in dedicated engines in order to properyl consume them (e.g. GIS, DBs, Catalogues, Data Analytics..)
 - data analytics

We can then visualize our document as passing through different <strong>PHASES</strong> of it lifecycle (e.g. DRAFT,APPROVED ...).
We call <strong>STEPs</strong> the operations that may later the PHASE of a project by : 
- performing a predefined operation on our document
- [optionally]triggering generic events (e.g. notifications)
- altering a Project lifecycle information (reporting outcome, status, messages etc.)

STEPS are implemented in <strong>LifecycleManager</strong> plugins.
The suite comes with a default set of a pre defined, general-purpose plugins that can help manage the user's project.
This set can be extended for custom implementations.

<strong>NB</strong> : Projects lifecycles are configured in linked Use Case Descriptors.\
Each Project starts in <strong>Draft</strong> PHASE and then changes according to configured Lifecycle Manager.

Once our request is ready we can send it to server with a <strong>POST</strong> request at <em>SERVICE_BASE_ENDPOINT</em>/projects/UCID/step/<strong>STEPID/<\strong><strong>ID</strong> where:\
- SERVICE_BASE_ENDPOINT should be discovered from the infrastructure's Information System
- UCID is the ID of the Use Case Descriptor to be used with this project
- ID is our project Unique Identifier
- ID is our project Unique Identifier

Depending on implementations and configurations, invoked STEP may expect/require some additional parameters.\
These can be specified in the request body as a simple JSON object.
Please refere to specific plugin documentation for details.

In [ ]:
#NB Assuming UCID = "basic"
#Prepare STEP execution request
STEPrequest={"stepID" : "PUBLISH"}
project= send(method="POST",dest=projects_endpoint+"/step/"+str(project["_id"]),data=json.dumps(STEPrequest))

print("Our resulting project new lifecycle information")
print_json(data=project["_lifecycleInformation"])

## Materialization
Learn how Filesets are materialized into enhanced resources (e.g. GIS Layers, DBMS Tables, Algorithms..)

As discussed above, Fileset may need to be managed in order to : 
- materialize them in dedicated engines in order to properyl consume them (e.g. GIS, DBs, Catalogues, Data Analytics..)
- perform data analytics tasks

If these processes generates some kind of consumable resources, they are registered in the Fileset as <strong>Materializations</strong>

If the above execution went well (check for errors in the displayed lifecycle information), our fileset should have been materialized as a layer in our infrastructure SDI.\
See below the enhanced fileset with new generated information about our new layer.

<strong>NB</strong> Each FileSet Materialization type has a different structure, in order to adapt to the needs of the application.

In [ ]:
print_json(data=project["_theDocument"]["section"]["fileset"])

### Gcube SDI Layers
<strong>GCUBE SDI Layers </strong>are materializations of a filesets in a gCube SDI.
They expose the following informations, allowing applications and users to consume the generated resources: 
- <strong>_ogcLinks</strong> : Open Geospatial Consortium standard URLs
- <strong>_bbox</strong>
- <strong>_platformInfo</strong> : collection of platform - specific JSON objects

Known platform info types are : 
- GeoServer
- GeoNetwork (TBD)
- Thredds (TBD)

Here is the layer generated in the above STEP execution

In [ ]:
#pipenv install arcgis
# try and visualize GIS 

In [ ]:
print_json(data=project["_theDocument"]["section"]["fileset"]["materializations"][0])

## Accessing Projects
The service allows for both access and querying against the internal Document archive.

### Querying

<strong>Queries</strong> can be perfomed with a <strong>POST</strong> HTTP Request at <em>SERVICE_BASE_ENDPOINT</em>/projects/<em>UCID</em>/<strong>query</strong> with a JSON body with the following fields : 
- <strong>filter</strong> : the JSON filter to apply (see MongoDB documentation for more details)
- <strong>projection</strong> : the target format to use to represent the returned JSON objects (see MongoDB documentation for more details)
- <strong>ordering</strong> : determines ordering behaviour 
-- <strong>direction</strong> : allowed values are <strong>ASCENDING</strong> and <strong>DESCENDING</strong>
-- <strong>fields</strong> : list of fields used for ordering
- <strong>paging</strong> : determines the paged request's window
-- <strong>offset</strong>
-- <strong>limit</strong>

This feature heavily relies on the underlying Document Store Engine, currently mongoDB.\
Please refer to mongoDB documentation for more details.

The following sections provide some Query example.

In [ ]:
#Query All
queryAll = {}

# Query All with PHASE = PUBLISHED
queryPublished = {
    "filter" : {"_lifecycleInformation._phase": {"$eq" : "PUBLISHED"}}
}
#ADD Ordering
queryOrdering = {
    "filter" : {"_lifecycleInformation._phase": {"$eq" : "PUBLISHED"}},
    "ordering" :{"direction":"ASCENDING","fields":[{"_theDocument.title"}]}
}
#GET ONLY FIRST ELEMENT
queryFirst = {
    "filter" : {"_lifecycleInformation._phase": {"$eq" : "PUBLISHED"}},
    "ordering" :{"direction":"ASCENDING","fields":[{"_theDocument.title"}]},
    "paging" : {"offset":0,"limit":1}
}
#GET ONLY TITLE AND AUTHOR
queryTitleAndAuthor = {
    "filter" : {"_lifecycleInformation._phase": {"$eq" : "PUBLISHED"}},
    "ordering" :{"direction":"ASCENDING","fields":[{"_theDocument.title"}]},
    "paging" : {"offset":0,"limit":1},
    "projection" :{"_theDocument.title":1,"_info.creationUser.username":1}
}

In [ ]:
#Actually performing query
found = send(dest=projects_endpoint+"/query",data=json.dumps(queryAll),method="POST")
print("Result Count :"+str(len(found)))

### Get By ID 

As standard REST agreement, Projects can be obtained by their ID with a <strong>POST</strong> HTTP Request at <em>SERVICE_BASE_ENDPOINT</em>/projects/<em>UCID</em>/<strong>ID</strong>

In [ ]:
#Lets take an id from previous query
projectId=found[0]["_id"]
project = send(method="GET",dest=projects_endpoint+projectId)
print_json(data=project)

### Runtime Configuration

Learn about how the service exposes information on how to access and consume generated resources.

As a collateral effect of workflow management, the following resources may be generated at runtime and managed by the service : 
- <strong>Uploaded file archive</strong> : Based on gCube Workspace
- <strong>Document archive</strong> : Document store based archive of Projects
- <strong>Indexes</strong> : GIS, Textual, Documental indexes, DBMS

These resources are not linked to one particular Project, but are related to the management of a specific UCD.\
Applications that need to access these resources (e.g. GUIs) can access a Configuration report at <em>SERVICE_BASE_ENDPOINT</em>/<strong>projects</strong>/UCID/configuration.

In [ ]:
print_json(data=send(dest=projects_endpoint+"/configuration",method="GET"))

# Use Case Descriptors - UCD

Use Case Descriptors (<strong>UCDs</strong>) are JSON documents containing the configuration settings needed for the management of our Projects, from the creation to their consumption.

In this section we are going to inspect both generic configurations (e.g. Data Access Policies) and some common Plugin configuration (e.g. Lifecycle Management)

In [ ]:
# loads UCD from service
queryUCDByID = {"filter" : {"_id":{"$eq":ucid}}}

UCD = send(method="POST",data=json.dumps(queryUCDByID),dest=ucd_endpoint+"query")

print_json(data=UCD)

## UCD Format
UCD content can be expanded in order to satisfy involved components needs, but its basic structure is fixed.

UCD most notable fields are : 
- <strong>_id</strong> : the Unique Identifier of the UCD
- <strong>_schema</strong> : the schema of the document to be handled in Projects (see "_theDocument") linked to this UCD
- <strong>_creationInfo</strong> : accounting information about author, time of creation, Infrastructure Context
- <strong>_dataAccessPolicies</strong> : access rules based on user Role
- <strong>_handlers</strong> : specific configurations for all involved components (both Plugins and GUIs)

In [ ]:
print_json(data=UCD)

### Schema

This section represents the expected structure of a managed <strong>Document</strong> inside a <strong>Project</strong> linked to the present UCD.

In general it's an optional section of a UCD, but most Handlers and features (e.g. FileSet operations) rely on this section.

It is represented as a map of extensible <strong>Field</strong> objects with <em>at least</em> the following information : 
- <strong>_type</strong> : <em>String</em>
- <strong>_max</strong> : <em>Integer</em> Maximum cardinality : (Default is 1)
- <strong>_min</strong> : <em>Integer</em> Minimum cardinality : (Default is 0)
- <strong>_label</strong> : <em>String</em> Human Readable Label
- <strong>_children</strong> : <em>Field Collection</em> Nested fields definition

In [ ]:
print_json(data=UCD["_schema"])

### Data Access Policies

<strong>Data Access Policies</strong> determine both <em>READ</em> and <em>WRITE</em> authorization on Projects, based on the user's <strong>Role</strong>

Section <em>_dataAccessPolicies</em> of UCD contains a list of <strong>Rules<strong> in the following format : 
- <strong>_policy</strong> [Mandatory] : contains read and write operation policy for the present Rule (allowed values are <strong>any</strong>,<strong>own</strong> and <strong>none</strong>)
- <strong>_roles</strong> [Mandatory] : Collections of users roles for witch the present Rule should be applied
- <strong>_enforcer</strong> : Additional conditions that should be always applied when accessing data (allowed value is <strong>filter</strong>)

E.g. 
The following rule : 
- Applies as default (no roles are specified)
- Denies any WRITE operation
- Allows read operations to any Project
- Filters any access to Projects selecting only the one which Phase is Published


```json
{"_policy" : {"_read" : "any", "_write" : "none"}, "_roles":[],
      "_enforcer": {"_filter" :  {"_lifecycleInformation._phase" :  {"$eq" :  "Published"}}}},
```

In [ ]:
print_json(data=UCD["_dataAccessPolicies"])

### Handlers Configuration

Handler configurations are simple JSON objects that wrap specific configuration for sw components that are going to consume our Projects.

Its default structure is : 
- <strong>_id</strong> : identifies the target plugin
- <strong>_type</strong> : declares the target plugin type
- <strong>_configuration</strong> : defines the actual plugin configuration (plugin specific)

Please refere to the specific plugin guide for more information

## Access and Querying
UCDs are also cached in the underlying document store Database, allwoing for the same querying capabilities as for Projects.

UCDs can be accessed by their cached MongoID at the following endpoint : <em>SERVICE_BASE_ENDPOINT</em>/ucd/<strong>MongoID</strong>

In [ ]:
#Perform get UCD by ID 
print_json(data=send(method="GET",dest=ucd_endpoint+str(UCD["_mongoId"])))

However, applications might want to perform one of the following queries or a more specific one.\
Check <em>Accessing Projects</em> section for more details.

In [ ]:
#Query BY UCID
query = {"filter" : {"_id":{"$eq":ucid}}}

In [ ]:
#Actually perform query
print(send(method="POST",data=query,dest=ucd_endpoint+"query"))

# Plugins

The CMS service itself only deals with generic logic of Projects lifecycle management. The actual hard work is performed by the <strong>Plugins</strong> configured in the linked <strong>Use Case Descriptor</strong>.

In more details, the the basic service logic relies on a <strong>Lifecycle Manager</strong> for the execution of <strong>STEPS</strong> and <strong>EVENT</strong> handling, which in turn <em>may</em> exploit other plugins for its purposes.\
Projects and document are only actually updated by the service logic, granting full centralized error management.

![Lifecycle](https://gcube.wiki.gcube-system.org/images_gcube/1/10/LC_Management.png)

In this section we are going to introduce some of the most common plugins that can be configured in UCDs.\
<strong>NB : Plugin set can be expanded by the community both from scratch and by extending the already implemented behaviour</strong>

## Lifecycle Managers
<strong>Lifecycle Managers</strong> are the main responsible for the execution of a <strong>Project workflow</strong>.

They define the support for <strong>STEPs</strong>, <strong>EVENTs</strong> and the resulting document <strong>PHASE</strong>, so basically they define the Workflow itself.

However customizable, workflows shares some basic behaviour : 
- Each Project starts in <strong>DRAFT</strong> PHASE, then it evolves depending on the configured Lifecycle Manager.
- The following EVENTS are always triggered (even if they can be implemented as NO-OP) :
  - ON INIT
  - ON UPDATE
  - ON DELETE
  - ON DELETE FILESET

<strong>NB</strong> : ROLE based access to STEPs is entrusted to Lifecycle Managers. Provided implementations exploit the feature <strong>BasicRoleManager</strong> documented below.

The service is distributed with some default implementations in order to provide support for common situations.

### DEFAULT-SINGLE-STEP
<strong>DEFAULT-SINGLE-STEP</strong> Lifecycle Manager is a simple workflow implementation consisting of a single STEP "Publish". 

PUBLISH step:
- materializes GIS Resources exploiting <strong>SDI-Default-Materializer</strong> plugin
- indexes GIS resources in a centroid layers exploiting </strong>SDI-Indexer-Plugin</strong> plugin
- sets the Project PHASE to "PUBLISHED"
- [optionally] sends notifications via </strong>Notification</strong> plugin 

The following events are also managed :
- ON INIT (basic validation, basic default values evaluation)
- ON UPDATE (basic validation, basic default values evaluation)
- ON DELETE (delete all materializations and index references)
- ON DELETE FILESET (delete Fileset materializations and update index references)

It exploits the feature <strong>BasicRoleManager</strong> documented below.

### DEFAULT-3PHASE
<strong>DEFAULT-3PHASE</strong> Lifecycle Manager is a moderated workflow implementation which allows for approval a rejection of submitted Drafts.

It can be summarized with the following diagram :

![3Phase](https://support.d4science.org/attachments/download/6070/3PhaseLC.png)

It is built on top of <strong>DEFAULT-SINGLE-STEP</strong>, extending its behavior in order to : 
- Manage different indexes (restricted and public) for documets in PHASES "Awaiting Approval" and "Published"
- Allow for iterative editing cycle between submitting user and moderators

It exploits the feature <strong>BasicRoleManager</strong> documented below.

### Basic Role Manager

Basic role manager is an internal feature of the CMS service. It restricts execution of STEPs based on user Role.
It reads the Lifecycle manager configuration expecting a collection of rules like in the following example.

The following configuration allows users with <em>Editor</em> role to only <em>SUBMIT</em> projects, while <em>Moderator</em> and <em>DataAdmin</em> can also <em>PUBLISH</em>

```json
{
      "_id" :  "DEFAULT-SINGLE-STEP",
      "_type" :  "LifecycleManagement",
      "_configuration" : {
          ...
        "step_access" : [
          {"STEP" : "PUBLISH", "roles" :[ "Moderator","DataAdmin"]},
          {"STEP" : "SUBMIT", "roles" :[ "Editor","Moderator","DataAdmin"]}
        ]
      }
    }
```

## Indexer Plugins
Indexer plugins are in charge of managing resources (<strong>Indexes</strong>)that contain references to the Projects in order to provide some kind of browsing experience through them.\
They use the information on the selected Project to manage Index entries and (optionally) generate <strong>spatialReferences</strong> and <strong>temporalReferences</strong>.

### SDI-Indexer-Plugin
This plugin manages centroids layers in the SDI GeoServer, generating the Project spatialReference.

It expects following <strong>UCD Handler Configuration</strong> : 
- <strong>bboxEvaluation</strong> Collection of JSONPaths to use in order to evaluate the Project centroid
- <strong>explicitFieldMapping</strong> Collection of JSON Object defining the centroid record fields along with JSONPath for their evaluation
- <strong>additionalLayers</strong> Collection of JSON Objects defining additional layers to use for cross-reference querying of the centroid layers

A typycal configuration might be as following : 
```json
    {
      "_id" : "SDI-Indexer-Plugin",
      "_type" : "Indexer",
      "_configuration" : {
        "bboxEvaluation" : ["$.._bbox"],
        "explicitFieldMapping" : [
          {"name" :  "titolo", "path" :  "$._theDocument.title", "type" : "TEXT"}
        ],
        "jslt" : {},
        "additionalLayers" : [
          {"source" : {"url" :  "..."},"toSetTitle":""}
        ]
      }
    }
```

It also expects the Lifecycle manager to provide the following call Parameters : 
- Indexing request
    - indexName : must be unique (table in postgis)
    - worksapce : GeoServer Workspace
    - centroidRecord : optionally declare the record to index instead of evaluating it

## Materializer Plugins
Materializer plugins are in charge of generating resources representing <strong>FileSets</strong>, and producing their references to be set in the Document itself.

### SDI-Indexer-Plugin
This plugin orchestrate the creation and publication of <strong>GIS Layers</strong> in the infrastructure's SDI, registering FileSets in its specific target engine (depending on data formats).

Currently supported data formats are : 
- SHP : shape files (along with SHX files if present)

It expects the following <strong>UCD Handler Configuration</strong> : 
- <strong>registeredFileSetPaths</strong> Collection of JSONPaths pairs pointing to the FileSets to be Materialized by this plugin.

A typycal configuration might be as following : 
```json
   {
      "_id" :  "SDI-Default-Materializer",
      "_type" :  "Materializer",
      "_configuration" : {
        "registeredFileSetPaths" : [
          {"schemaField" :  "pianteFineScavo","documentPath" :  "pianteFineScavo[*].fileset"},
          {"schemaField" :  "posizionamentoScavo","documentPath" :  "posizionamentoScavo.fileset"}
        ]
      }
    }
```

## Getting installed plugins
The service allows for inspaction and management of installed plugins.

Installed plugins descriptors can be obtained at SERVICE_BASE_ENDPOINT/<strong>plugins</strong> and SERVICE_BASE_ENDPOINT/plugins/<strong>pluginID</strong>

In [ ]:
print_json(data=send(method="GET",dest=plugins_endpoint))